In [1]:
import sys, time, pickle, torch
sys.path.insert(0, '../Models')
sys.path.insert(0, '../Utils')
sys.path.insert(0, '../Preprocess')
import numpy as np
import pandas as pd
from ann import NeuralNet
from utils import my_completely_random_sample, conv_input_attri_to_word_attri,\
    collect_info_for_metric, save_info, random_state
from preprocess_funcs import preprocess_pipelined, prepare_text, prepare_text_view_friendly
from nltk.tokenize import word_tokenize

[nltk_data] Downloading package stopwords to /home/user/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /home/user/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
model = torch.load('../Models/ann_model.pt')

In [3]:
Train_df = pd.read_csv('../Data/Processed/train_df.csv')
Test_df = pd.read_csv('../Data/Processed/test_df.csv')
Y_train = Train_df['sentiment']
Y_test = Test_df['sentiment']
Y_train_tensor = torch.tensor(Y_train, dtype=torch.float).unsqueeze(dim=1)
Y_test_tensor = torch.tensor(Y_test, dtype=torch.float).unsqueeze(dim=1)


In [4]:
reviews_raw, targets, indices = my_completely_random_sample(Train_df, num_sample=10)

In [5]:
reviews_raw[0]

'This musical was not quite what I expected, foremost being there weren\'t many scenes between Brando and Sinatra. As it was based on a Damon Runyon story, I expected irony and surprise, of which there was one really good one - when we find that Sinatra\'s gang has used the Salvation Army office for their crap game while Brando was in Havana with Simmons. If course it comes at the right moment too, when Brando brings her back. I really didn\'t expect much from Brando as a singer, but he surprised me. He wasn\'t great but he was just fine in the role. His big number in the sewer, however, with the rest of Sinatra\'s boys was the only place I felt Brando\'s voice was weak. He just didn\'t have the power the grand climax demanded. Overall I found the scenes between Brando and Simmons to be filled with electricity, something I didn\'t think would happen when we first see Simmons by herself, and later when we\'re introduced to Brando in the restaurant with Sinatra trying to pull a fast one 

In [6]:
#define some containers to save some info
model_out_list, attr_list = [], []

In [7]:
from captum.attr import Lime
from captum.attr import visualization 

In [8]:
lime = Lime(forward_func=model.forward)

In [9]:
def generate_record(raw_review, target):
    data, data_vec, input_tfidf = preprocess_pipelined([raw_review]) #preprocess_pipelined expects a lits of strings        
    input_model = input_tfidf.to_dense()
    with torch.no_grad():
        pred_prob =  model.forward(input_model).detach().item()
        pred_class = 'Pos' if pred_prob > 0.5 else 'Neg' 
        true_class = 'Pos' if target > 0.5 else 'Neg' 
        attribution = lime.attribute(input_model, n_samples=5000, return_input_shape=True, show_progress=True)
        attr_score = torch.sum(attribution)    
        attr_class = 'Pos' if attr_score > 0.5 else 'Neg'
        raw_input = word_tokenize(raw_review) #raw_review.split()
        convergence_score = 0
        word_attributions = conv_input_attri_to_word_attri(attribution, raw_review)
        #         print(f'word attributions {word_attributions}')
        #         print(f'pred_prob {pred_prob}')
        #         print(f'pred_class {pred_class}')
        #         print(f'true_class {true_class}')
        #         print(f'attribution {attribution}')
        #         print(f'attr_class {attr_class}')
        #         print(f'attr_score {attr_score}')
#         print(f'raw_input {raw_input}')

        
        #collect info for metrics later
        collect_info_for_metric(model_out_list, pred_prob, attr_list, attribution)
        
    
        visual_record = visualization.VisualizationDataRecord(word_attributions=word_attributions,
                                                         pred_prob=pred_prob,
                                                         pred_class=pred_class,
                                                         true_class=true_class,
                                                         attr_class=attr_class,
                                                         attr_score=attr_score,
                                                         raw_input=raw_input,
                                                         convergence_score=convergence_score)
        
        
        return visual_record
      
    

In [10]:
for i, (rev_raw, target) in enumerate(zip(reviews_raw, targets)):
    visual_record = generate_record(rev_raw, target)
    print(visualization.visualize_text([visual_record])) #list because visualize_text expects a list of visual_records


/home/user/anaconda3/envs/py38/lib/python3.9/site-packages/torch/nn/functional.py:1806: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")
/home/user/anaconda3/envs/py38/lib/python3.9/site-packages/captum/attr/_core/lime.py:1088: UserWarning: Attempting to construct interpretable model with > 10000 features.This can be very slow or lead to OOM issues. Please provide a featuremask which groups input features to reduce the number of interpretablefeatures. 
  warnings.warn(
Lime attribution: 100%|████████████████████████████████████████████████████████████| 5000/5000 [00:11<00:00, 451.34it/s]


words attr: {'great': tensor(0.4935), 'simmons': tensor(0.9389), 'sinatra': tensor(1.)}


/home/user/anaconda3/envs/py38/lib/python3.9/site-packages/torch/nn/functional.py:1806: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")
/home/user/anaconda3/envs/py38/lib/python3.9/site-packages/captum/attr/_core/lime.py:1088: UserWarning: Attempting to construct interpretable model with > 10000 features.This can be very slow or lead to OOM issues. Please provide a featuremask which groups input features to reduce the number of interpretablefeatures. 
  warnings.warn(


<IPython.core.display.HTML object>


Lime attribution: 100%|████████████████████████████████████████████████████████████| 5000/5000 [00:10<00:00, 460.38it/s]


...

/home/user/anaconda3/envs/py38/lib/python3.9/site-packages/torch/nn/functional.py:1806: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")
/home/user/anaconda3/envs/py38/lib/python3.9/site-packages/captum/attr/_core/lime.py:1088: UserWarning: Attempting to construct interpretable model with > 10000 features.This can be very slow or lead to OOM issues. Please provide a featuremask which groups input features to reduce the number of interpretablefeatures. 
  warnings.warn(


<IPython.core.display.HTML object>


Lime attribution: 100%|████████████████████████████████████████████████████████████| 5000/5000 [00:10<00:00, 467.81it/s]


words attr: {'bad': tensor(-1.), 'dreadful': tensor(-0.0357), 'excuse': tensor(-0.0868), 'gymkata': tensor(-0.3866), 'mst3k': tensor(-0.1422)}


<IPython.core.display.HTML object>


In [11]:
save_info(indices, reviews_raw, targets, model_out_list, attr_list, fname='lime_outs.pkl')

{'indices': [3555,
  23474,
  13833,
  12237,
  4632,
  9114,
  327,
  844,
  24631,
  17758,
  5654,
  19637,
  1462,
  24567,
  8536,
  1013,
  13913,
  8203,
  12999,
  20936,
  10982,
  866,
  22731,
  19996,
  6293,
  18922,
  13688,
  12690,
  24838,
  3707,
  5811,
  5400,
  3285,
  2277,
  4026,
  15629,
  12084,
  14787,
  2421,
  13503,
  21742,
  338,
  18429,
  14404,
  7464,
  8679,
  16240,
  20882,
  15145,
  6782,
  13615,
  24420,
  8581,
  21797,
  10057,
  15051,
  21480,
  153,
  18810,
  16401,
  8940,
  12167,
  21933,
  22489,
  14061,
  1267,
  24227,
  5876,
  19832,
  11042,
  7307,
  23696,
  3962,
  16021,
  10652,
  75,
  11424,
  74,
  22711,
  10178,
  18522,
  1427,
  11155,
  5434,
  7696,
  21546,
  24579,
  17529,
  21464,
  15887,
  12967,
  7162,
  19841,
  2706,
  21057,
  4097,
  4939,
  15201,
  2310,
  18632],
 'raw_reviews': ['This musical was not quite what I expected, foremost being there weren\'t many scenes between Brando and Sinatra. As it

In [12]:
# 

In [13]:
# from lime.lime_text import LimeTextExplainer
# explainer = LimeTextExplainer(
#     class_names = ['negative', 'positive'],
#     bow=True
#   )

# def lime_pred_sentence(sentence):
#     if isinstance(sentence, str):
#         sentence = [sentence]
#     sent_prepped, sent_vec, sent_tensor = preprocess_pipelined(sentence)
#     print(f'sent tensor size {sent_tensor.size()}')
#     with torch.no_grad():
#         out = model(sent_tensor)
#         out_complement = 1-out
#         out_concat = torch.cat([out_complement, out], dim=1)
#         out_concat_np = out_concat.detach().numpy()
    
# #         print(f'{sent_prepped}')
# #         print(f'{sent_vec}')
# #         print(f'{sent_tensor}')
# #         print(f'{out_concat_np.shape}')
#         return out_concat_np

# for r in reviews_raw:
#     explanation = explainer.explain_instance(r, lime_pred_sentence)
#     explanation.show_in_notebook()